In [2]:

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import json

In [ ]:
df=pd.read_csv('/content/analogud.csv')
df

Time [s]  Channel 0
0      0.001058      0.143
1      0.001059      0.148
2      0.001059      0.148
3      0.001060      0.153
4      0.001061      0.153
...         ...        ...
90576  0.059027      1.978
90577  0.059027      2.030
90578  0.059028      1.937
90579  0.059029      1.691
90580  0.059029      1.315

[90581 rows x 2 columns]

In [ ]:
df['Index'] = df.index/1000
df

Time [s]  Channel 0   Index
0      0.001058      0.143   0.000
1      0.001059      0.148   0.001
2      0.001059      0.148   0.002
3      0.001060      0.153   0.003
4      0.001061      0.153   0.004
...         ...        ...     ...
90576  0.059027      1.978  90.576
90577  0.059027      2.030  90.577
90578  0.059028      1.937  90.578
90579  0.059029      1.691  90.579
90580  0.059029      1.315  90.580

[90581 rows x 3 columns]

In [ ]:
import plotly.express as px
fig = px.line(df, x = "Index",
              y = "Channel 0" )
fig.show()

In [ ]:
a=[]
print(len(df))
for i in df['Index']:
  if i< 13.96:         #13.8
    a.append('IBG')
  elif i>=13.96 and i<14.483:
     a.append('Preamble')
  elif i>=14.483 and i<66.571:
    a.append('Record')
  elif i>=66.571 and i<67.1:
    a.append('Postamble')
  elif i>=67.1 and i<80.027:
    a.append('IBG')
  elif i>=80.027 and i<80.536:  #79.95
    a.append('Preamble')
  elif i>=80.536:
    a.append('Record')

print(len(a))
df['Target']=a

90581
90581


In [ ]:
import plotly.express as px
fig = px.line(df, x = "Index",
              y = "Target")

fig.show()

In [ ]:
import plotly.express as px
fig = px.line(df, x = "Index",y = "Channel 0",color = "Target")
fig.show()

In [ ]:
df

Time [s]  Channel 0   Index  Target
0      0.001058      0.143   0.000     IBG
1      0.001059      0.148   0.001     IBG
2      0.001059      0.148   0.002     IBG
3      0.001060      0.153   0.003     IBG
4      0.001061      0.153   0.004     IBG
...         ...        ...     ...     ...
90576  0.059027      1.978  90.576  Record
90577  0.059027      2.030  90.577  Record
90578  0.059028      1.937  90.578  Record
90579  0.059029      1.691  90.579  Record
90580  0.059029      1.315  90.580  Record

[90581 rows x 4 columns]

In [ ]:
from sklearn.preprocessing import LabelEncoder
labelencoder = LabelEncoder()
df['T'] = labelencoder.fit_transform(df['Target'])
df

Time [s]  Channel 0   Index  Target  T
0      0.001058      0.143   0.000     IBG  0
1      0.001059      0.148   0.001     IBG  0
2      0.001059      0.148   0.002     IBG  0
3      0.001060      0.153   0.003     IBG  0
4      0.001061      0.153   0.004     IBG  0
...         ...        ...     ...     ... ..
90576  0.059027      1.978  90.576  Record  3
90577  0.059027      2.030  90.577  Record  3
90578  0.059028      1.937  90.578  Record  3
90579  0.059029      1.691  90.579  Record  3
90580  0.059029      1.315  90.580  Record  3

[90581 rows x 5 columns]

In [ ]:
df.to_csv('dataset.csv')

In [ ]:
import pandas as pd
import numpy as np
from tensorflow.keras.utils import to_categorical

def load_and_preprocess(csv_file, window_size=50, num_classes=4):
    df = pd.read_csv(csv_file)
    signal = df['Channel 0'].values
    labels = df['T'].values

    X, y = [], []
    for i in range(len(signal) - window_size + 1):
        X.append(signal[i:i+window_size])
        y.append(labels[i:i+window_size])

    X = np.array(X)[..., np.newaxis]  # shape: (num_samples, window_size, 1)
    y = to_categorical(y, num_classes=num_classes)  # shape: (num_samples, window_size, num_classes)
    return X, y,signal,labels


In [ ]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, TimeDistributed, Input, Masking, Bidirectional

def build_model(input_shape, num_classes):
    model = Sequential([
        Input(shape=input_shape),
        Bidirectional(LSTM(64, return_sequences=True)),
        TimeDistributed(Dense(num_classes, activation='softmax'))
    ])
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model


In [ ]:
X, y,full_signal, full_labels = load_and_preprocess('dataset.csv', window_size=50, num_classes=4)
model = build_model(input_shape=(50, 1), num_classes=4)
model.summary()
model.fit(X, y, epochs=3, batch_size=16)

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ bidirectional (Bidirectional)   │ (None, 50, 128)        │        33,792 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ time_distributed                │ (None, 50, 4)          │           516 │
│ (TimeDistributed)               │                        │               │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 34,308 (134.02 KB)

 Trainable params: 34,308 (134.02 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/3
5659/5659 ━━━━━━━━━━━━━━━━━━━━ 259s 44ms/step - accuracy: 0.9626 - loss: 0.1337
Epoch 2/3
5659/5659 ━━━━━━━━━━━━━━━━━━━━ 263s 45ms/step - accuracy: 0.9837 - loss: 0.0708
Epoch 3/3
2926/5659 ━━━━━━━━━━━━━━━━━━━━ 2:01 44ms/step - accuracy: 0.9855 - loss: 0.0613

In [ ]:
dftest = pd.read_csv('analogt.csv')
dftest

Time [s]  Channel 1
0      -0.006543      0.141
1      -0.006543      0.125
2      -0.006542      0.120
3      -0.006541      0.125
4      -0.006541      0.141
...          ...        ...
140905  0.083636      0.084
140906  0.083637      0.084
140907  0.083637      0.084
140908  0.083638      0.089
140909  0.083638      0.094

[140910 rows x 2 columns]

In [ ]:
import pandas as pd
import numpy as np
from tensorflow.keras.utils import to_categorical

def load_and_preprocesst(signal, window_size=50, num_classes=4):
    X = []
    for i in range(len(signal) - window_size + 1):
        X.append(signal[i:i+window_size])


    X = np.array(X)[..., np.newaxis]  # shape: (num_samples, window_size, 1)

    return X


In [ ]:
# Predict
Xt=dftest['Channel 1'].values
Xte=load_and_preprocesst(Xt, window_size=50, num_classes=4)
y_pred_probs = model.predict(Xte)  # (samples, window, classes)
y_pred = np.argmax(y_pred_probs, axis=-1)  # Convert softmax to class index

4402/4402 ━━━━━━━━━━━━━━━━━━━━ 39s 9ms/step


In [ ]:
def reconstruct_full_prediction(y_pred_seq, total_length, window_size):
    counts = np.zeros((total_length, 4))
    for i, seq in enumerate(y_pred_seq):
        for j, tag in enumerate(seq):
            counts[i + j, tag] += 1
    return np.argmax(counts, axis=1)[:total_length]


In [ ]:
predicted_full_labels = reconstruct_full_prediction(y_pred, len(Xt), window_size=50)


In [ ]:
predicted_full_labels.shape

(140910,)

In [ ]:
dftest['Target']=predicted_full_labels
dftest['Index'] = dftest.index/1000
dftest

Time [s]  Channel 1  Target    Index
0      -0.006543      0.141       0    0.000
1      -0.006543      0.125       0    0.001
2      -0.006542      0.120       0    0.002
3      -0.006541      0.125       0    0.003
4      -0.006541      0.141       0    0.004
...          ...        ...     ...      ...
140905  0.083636      0.084       0  140.905
140906  0.083637      0.084       0  140.906
140907  0.083637      0.084       0  140.907
140908  0.083638      0.089       0  140.908
140909  0.083638      0.094       0  140.909

[140910 rows x 4 columns]

In [ ]:
import plotly.express as px
fig = px.line(dftest, x = "Index",y = "Channel 1",color = "Target")
fig.show()

In [ ]:
dftest.to_csv('datasettarget.csv')

In [3]:
dftarget=pd.read_csv('/content/datasettarget.csv')

In [4]:
# Preamble Peak
for i in dftarget.index:
  if dftarget['Target'].iloc[i]==2:
    x=1
  if dftarget['Target'].iloc[i]==3 and dftarget['Channel 1'].iloc[i]>1.5 and x==1:
    print(i)
    x=0

10741
76793


In [5]:
# Preamble Valley
for i in dftarget.index:
  if dftarget['Target'].iloc[i]==2:
    x=1
  if dftarget['Target'].iloc[i]==3 and dftarget['Channel 1'].iloc[i]<-2 and x==1:
    print(i)
    x=0

10728
76782


In [6]:
# Postamble Peak
for i in dftarget.index:
  if dftarget['Target'].iloc[i]==3:
    x=1
  if dftarget['Target'].iloc[i]==1 and x==1:
    while dftarget['Channel 1'].iloc[i]<1.5:
      i-=1
    print(i)
    x=0

62817
127906


In [7]:
# Postamble Valley
for i in dftarget.index:
  if dftarget['Target'].iloc[i]==3:
    x=1
  if dftarget['Target'].iloc[i]==1 and x==1:
    while dftarget['Channel 1'].iloc[i]>-1.5:
      i-=1
    print(i)
    x=0

62806
127657


In [ ]:
for i in dftest['Target'].values:
  if i==0:
    print('IBG')
  elif i==1:
    print('Preamble')
  elif i==2:
    print('Record')
  elif i==3:
    print('Postamble')

Streaming output truncated to the last 5000 lines.
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
IBG
I

In [ ]:
import array
import struct
import sys
from collections import namedtuple

TYPE_DIGITAL = 0
TYPE_ANALOG = 1
expected_version = 0

AnalogData = namedtuple('AnalogData', ('begin_time', 'sample_rate', 'downsample', 'num_samples', 'samples'))

def parse_analog(f):
    # Parse header
    identifier = f.read(8)
    if identifier != b"<SALEAE>":
        raise Exception("Not a saleae file")

    version, datatype = struct.unpack('=ii', f.read(8))

    if version != expected_version or datatype != TYPE_ANALOG:
        raise Exception("Unexpected data type: {}".format(datatype))

    # Parse analog-specific data
    begin_time, sample_rate, downsample, num_samples = struct.unpack('=dqqq', f.read(32))

    # Parse samples
    samples = array.array("f")
    samples.fromfile(f, num_samples)

    return AnalogData(begin_time, sample_rate, downsample, num_samples, samples)


if __name__ == '__main__':
    filename = 'analog_1.bin'
    print("Opening " + filename)

    with open(filename, 'rb') as f:
        data = parse_analog(f)

    # Print out all analog data
    print("Begin time: {}".format(data.begin_time))
    print("Sample rate: {}".format(data.sample_rate))
    print("Downsample: {}".format(data.downsample))
    print("Number of samples: {}".format(data.num_samples))

    print("  {0:>20} {1:>10}".format("Time", "Voltage"))
    t=[]
    v=[]
    a={}
    for idx, voltage in enumerate(data.samples):
        sample_num = idx * data.downsample
        time = data.begin_time + (float(sample_num) / data.sample_rate)
        #print("  {0:>20} {1:>10}".format(time, voltage))
        t.append(time)
        v.append(voltage)
a['voltage']=v
a['time']=t
dft=pd.DataFrame(a)
dft

Opening analog_1.bin
Begin time: 40.17940032
Sample rate: 1562500
Downsample: 1
Number of samples: 18544825
                  Time    Voltage


KeyboardInterrupt: 

In [ ]:
dft[-200000:-100000].to_csv('datasettest.csv')

In [ ]:
Xt = load_and_preprocesst('datasettest.csv', window_size=50, num_classes=4)
yt=model.predict(Xt)

3124/3124 ━━━━━━━━━━━━━━━━━━━━ 44s 14ms/step


In [ ]:
yt
for i in yt:
  for j in i:
    print(np.argmax(j))

Streaming output truncated to the last 5000 lines.
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0

In [ ]:
import plotly.express as px
fig = px.line(ft, x = "time",y = "voltage",color = "Tar")
fig.show()

ValueError: Length of values (2) does not match length of index (999999)